In [ ]:
import matplotlib.pyplot as plt
import tensorflow as tf
import seaborn as sns
import random
from PIL import Image
from tensorflow.keras.preprocessing import image
from tensorflow.keras.applications.inception_v3 import InceptionV3
from tensorflow.keras import Sequential, Model
from keras.layers import (Conv2D, MaxPooling2D, Dense, Flatten, \
                          Dropout, Input,GlobalAveragePooling2D,BatchNormalization)
from tensorflow.keras.activations import softmax
from tensorflow.keras.optimizers import Adam
from keras.preprocessing.image import ImageDataGenerator
from mpl_toolkits.axes_grid1 import ImageGrid
from keras.models import Model
from keras.applications.vgg16 import VGG16, preprocess_input
from keras.callbacks import ModelCheckpoint, EarlyStopping
from sklearn.metrics import (ConfusionMatrixDisplay, confusion_matrix,
                             accuracy_score)
import cv2
import matplotlib.pyplot as plt
import tensorflow as tf
import seaborn as sns
import random
from PIL import Image
from tensorflow.keras.preprocessing import image
from tensorflow.keras.applications.inception_v3 import InceptionV3
from tensorflow.keras import Sequential, Model
from keras.layers import (Conv2D, MaxPooling2D, Dense, Flatten,
                          Dropout, Input,GlobalAveragePooling2D,BatchNormalization)
from tensorflow.keras.activations import softmax
from tensorflow.keras.optimizers import Adam
from keras.preprocessing.image import ImageDataGenerator
from mpl_toolkits.axes_grid1 import ImageGrid
from keras.models import Model
from keras.applications.vgg16 import VGG16, preprocess_input
from keras.callbacks import ModelCheckpoint, EarlyStopping
from sklearn.metrics import (ConfusionMatrixDisplay, confusion_matrix, accuracy_score)
# Base Libraries
from tensorflow.keras.applications import  VGG19,EfficientNetB0,VGG16,InceptionV3,ResNet50,EfficientNetB3
from tensorflow.keras.models import Model
from keras.applications.vgg16 import preprocess_input
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import os
# Transformation
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import power_transform
from sklearn.pipeline import Pipeline
# Feature Selection


from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor


#### Tes 4

In [3]:
import os
import random
import numpy as np
import pandas as pd
import cv2
import matplotlib.pyplot as plt
from tensorflow.keras.preprocessing import image
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Flatten, Conv2D, MaxPooling2D
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import ModelCheckpoint, ReduceLROnPlateau
from sklearn.model_selection import train_test_split, KFold
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import train_test_split, KFold
from tensorflow.keras.utils import to_categorical

# Define categories
cat = [
    'Acne and Rosacea',
    'Actinic Keratosis Basal Cell Carcinoma and other Malignant Lesions',
    'Atopic Dermatitis',
    'Bullous Disease',
    'Cellulitis Impetigo and other Bacterial Infections',
    'Eczema',
    'Exanthems and Drug Eruptions',
    'Hair Loss Photos Alopecia and other Hair Diseases',
    'Herpes HPV and other STDs',
    'Light Diseases and Disorders of Pigmentation',
    'Lupus and other Connective Tissue Diseases',
    'Melanoma Skin Cancer Nevi and Moles',
    'Nail Fungus and other Nail Disease',
    'Poison Ivy Photos and other Contact Dermatitis',
    'Psoriasis pictures Lichen Planus and Related Diseases',
    'Scabies Lyme Disease and other Infestations and Bites',
    'Seborrheic Keratoses and other Benign Tumors',
    'Systemic Disease',
    'Tinea Ringworm Candidiasis and other Fungal Infections',
    'Urticaria Hives',
    'Vascular Tumors',
    'Vasculitis Photos',
    'Warts Molluscum and other Viral Infections'
]

# Data dictionary function (improved for efficiency)
def data_dictionary():
    path_train = "./train/"
    train_df = pd.DataFrame(columns=["image_path", "target"])
    for i, category in enumerate(cat):
        path_disease_train = os.path.join(path_train, category)
        for img_path in os.listdir(path_disease_train):
            train_df = train_df.append({"image_path": os.path.join(path_disease_train, img_path), "target": i}, ignore_index=True)
    return train_df


# Load data using ImageDataGenerator (avoid loading all images at once)
train = data_dictionary()
train_datagen = ImageDataGenerator(rescale=1./255.0)  # Normalize images

train_generator = train_datagen.flow_from_dataframe(
    train,
    directory="./train/",
    x_col="image_path",
    y_col="target",
    target_size=(180, 180),
    batch_size=32,  # Adjust batch size based on memory constraints
    class_mode="categorical"
)

# Define the model (same as before)
model = Sequential([
    Conv2D(32, (3, 3), activation='relu', input_shape=(180, 180, 3)),
    MaxPooling2D((2, 2)),
    Conv2D(64, (3, 3), activation='relu'),
    MaxPooling2D((2, 2)),
    Conv2D(128, (3, 3), activation='relu'),
    MaxPooling2D((2, 2)),
    Flatten(),
    Dense(512, activation='relu'),
    Dense(256, activation='relu'),
    Dense(128, activation='relu'),
    Dense(23, activation='softmax'),
])

# Compile the model
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

# Train the model with K-Fold Cross-Validation
kf = KFold(n_splits=3)
for i, (train_index, val_index) in enumerate(kf.split(train)):
    # Train using data generator (don't load all data at once)
    train_generator.reset_index(drop=True)  # Reset generator for each fold
    val_generator = train_datagen.flow_from_dataframe(
        train.iloc[val_index],
        directory="./train/",
        x_col="image_path",
        y_col="target",
        target_size=(180, 180),
        batch_size=32,
        class_mode="categorical"
    )

    # Train the model
    history = model.fit(train_generator, epochs=15, validation_data=val_generator)

    # Evaluate the model (optional, can be done after all folds)
    loss, accuracy = model.evaluate(val_generator)
    print(f"Fold {i+1} - Validation Accuracy: {accuracy:.4f}, Validation Loss: {loss:.4f}")

# Save the model
model.save('23class.h5')

# Plot training history
plt.figure(figsize=(12, 4))

# Plotting the accuracy
plt.subplot(1, 2, 1)
plt.plot(history.history['accuracy'], label='Training Accuracy')
plt.plot(history.history['val_accuracy'], label='Validation Accuracy')
plt.title('Accuracy')
plt.xlabel('Epoch')
plt.ylabel('Accuracy')
plt.legend()

# Plotting the loss
plt.subplot(1, 2, 2)
plt.plot(history.history['loss'], label='Training Loss')
plt.plot(history.history['val_loss'], label='Validation Loss')
plt.title('Loss')
plt.xlabel('Epoch')
plt.ylabel('Loss')
plt.legend()

plt.show()


C:\Users\Asus\AppData\Local\Temp\ipykernel_19608\953682729.py:51: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  train_df = train_df.append({"image_path": os.path.join(path_disease_train, img_path), "target": i}, ignore_index=True)
C:\Users\Asus\AppData\Local\Temp\ipykernel_19608\953682729.py:51: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  train_df = train_df.append({"image_path": os.path.join(path_disease_train, img_path), "target": i}, ignore_index=True)
C:\Users\Asus\AppData\Local\Temp\ipykernel_19608\953682729.py:51: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  train_df = train_df.append({"image_path": os.path.join(path_disease_train, img_path), "target": i}, ignore_index=True)
C:\Users\Asus\AppData\Local\Temp\ipykern

NameError: name 'ImageDataGenerator' is not defined

#### Tes 5

# PISAH

In [29]:
import matplotlib.pyplot as plt
import tensorflow as tf
import seaborn as sns
import random
from PIL import Image
from tensorflow.keras.preprocessing import image
from tensorflow.keras.applications.inception_v3 import InceptionV3
from tensorflow.keras import Sequential, Model
from tensorflow.keras.layers import (Conv2D, MaxPooling2D, Dense, Flatten, \
                          Dropout, Input,GlobalAveragePooling2D,BatchNormalization)
from tensorflow.keras.activations import softmax
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from mpl_toolkits.axes_grid1 import ImageGrid
from tensorflow.keras.applications.vgg16 import VGG16, preprocess_input
from tensorflow.keras.callbacks import ModelCheckpoint, EarlyStopping
from sklearn.metrics import (ConfusionMatrixDisplay, confusion_matrix, 
                             accuracy_score)
import cv2
import numpy as np 
import pandas as pd
import os
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import power_transform
from sklearn.pipeline import Pipeline
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor


In [30]:
train2=os.listdir("train")
train2

['Acne and Rosacea',
 'Actinic Keratosis Basal Cell Carcinoma and other Malignant Lesions',
 'Atopic Dermatitis',
 'Bullous Disease',
 'Cellulitis Impetigo and other Bacterial Infections',
 'Eczema',
 'Exanthems and Drug Eruptions',
 'Hair Loss Photos Alopecia and other Hair Diseases',
 'Herpes HPV and other STDs',
 'Light Diseases and Disorders of Pigmentation',
 'Lupus and other Connective Tissue Diseases',
 'Melanoma Skin Cancer Nevi and Moles',
 'Nail Fungus and other Nail Disease',
 'Poison Ivy Photos and other Contact Dermatitis',
 'Psoriasis pictures Lichen Planus and Related Diseases',
 'Scabies Lyme Disease and other Infestations and Bites',
 'Seborrheic Keratoses and other Benign Tumors',
 'Systemic Disease',
 'Tinea Ringworm Candidiasis and other Fungal Infections',
 'Urticaria Hives',
 'Vascular Tumors',
 'Vasculitis Photos',
 'Warts Molluscum and other Viral Infections']

In [ ]:
# cat2=['Melanoma Skin Cancer Nevi and Moles']

In [31]:
cat=['Acne and Rosacea',
 'Actinic Keratosis Basal Cell Carcinoma and other Malignant Lesions',
 'Atopic Dermatitis',
 'Bullous Disease',
 'Cellulitis Impetigo and other Bacterial Infections',
 'Eczema',
 'Exanthems and Drug Eruptions',
 'Hair Loss Photos Alopecia and other Hair Diseases',
 'Herpes HPV and other STDs',
 'Light Diseases and Disorders of Pigmentation',
 'Lupus and other Connective Tissue Diseases',
 'Melanoma Skin Cancer Nevi and Moles',
 'Nail Fungus and other Nail Disease',
 'Poison Ivy Photos and other Contact Dermatitis',
 'Psoriasis pictures Lichen Planus and Related Diseases',
 'Scabies Lyme Disease and other Infestations and Bites',
 'Seborrheic Keratoses and other Benign Tumors',
 'Systemic Disease',
 'Tinea Ringworm Candidiasis and other Fungal Infections',
 'Urticaria Hives',
 'Vascular Tumors',
 'Vasculitis Photos',
 'Warts Molluscum and other Viral Infections']

### Data dictionary function

In [ ]:
def data_dictionary():
    path_train = "./train/"
    path_test = "./test/"
    list_train = cat
    # list_train1 = cat2
    train_dictionary = {"image_path": [], "target": []}
    
    k = 0
    for i in list_train:
        path_disease_train = os.path.join(path_train, i)
        image_list_train = os.listdir(path_disease_train)
        for j in image_list_train:
            img_path_train = os.path.join(path_disease_train, j)
            train_dictionary["image_path"].append(img_path_train)
            train_dictionary['target'].append(k)
        k += 1
    
    for i in list_train1:
        path_disease_test = os.path.join(path_test, i)
        image_list_test = os.listdir(path_disease_test)
        for j in image_list_test:
            img_path_test = os.path.join(path_disease_test, j)
            train_dictionary["image_path"].append(img_path_test)
            train_dictionary['target'].append(k)  # Fix target label to the correct category
    train_df = pd.DataFrame(train_dictionary)
    return train_df

In [ ]:
train = data_dictionary()
train.info()

#### Load images and labels

In [ ]:

images = []
labels = []
for i in train['image_path']:
    img = cv2.imread(i)
    img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
    img = cv2.resize(img, (180, 180))
    images.append(img)

#### Plot example images

In [ ]:
example_list = [image for image in random.sample(images, k=6)]
fig, axes = plt.subplots(2, 3, figsize=(10, 8))

for ax, img_array in zip(axes.ravel(), example_list):
    ax.imshow(img_array)
    ax.axis('off')

plt.show()

In [ ]:
# label=train['target']
labels = train['target'].to_numpy()
print("Max label value:", np.max(labels))

In [ ]:
len(labels)

In [ ]:
len(images)

In [ ]:
data = np.array(images)
labels = np.array(labels)

In [ ]:
data.shape

In [ ]:
labels.shape

!pip install sklearn_relief

In [ ]:
vgg_model = VGG19(weights = 'imagenet',  include_top = False, input_shape = (180, 180, 3))

# let's make all layers non-trainable
for layer in vgg_model.layers :
    layer.trainable = False

from keras.utils.vis_utils import plot_model
plot_model(vgg_model, to_file='model_plot.png', show_shapes=True, show_layer_names=True)

In [ ]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D,MaxPooling2D,Flatten, Dense


#### Verify label ranges

In [ ]:
from sklearn.model_selection import train_test_split, KFold
from tensorflow.keras.utils import to_categorical

num_classes = 23  # Updated number of classes to 23
assert np.max(labels) < num_classes, "Label index out of range. Check the labels."

# Convert labels to categorical
labels = to_categorical(labels, num_classes)


#### Define the model

In [ ]:
model = Sequential([
    Dense(200, activation='relu'),
    Dense(170, activation='relu'),
    Dense(num_classes, activation='softmax'),
])

In [ ]:
from tensorflow.keras.callbacks import ModelCheckpoint, ReduceLROnPlateau

# Compile the model
mcp_save = ModelCheckpoint('EnetB0_CIFAR10_TL.h5', save_best_only=True, monitor='val_acc')
reduce_lr = ReduceLROnPlateau(monitor='val_acc', factor=0.5, patience=2, verbose=1)
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

In [ ]:
# from keras.callbacks import ModelCheckpoint, ReduceLROnPlateau

# mcp_save = ModelCheckpoint('EnetB0_CIFAR10_TL.h5', save_best_only=True, monitor='val_acc')
# reduce_lr = ReduceLROnPlateau(monitor='val_acc', factor=0.5, patience=2, verbose=1,)
# model.compile(optimizer='adam',loss='categorical_crossentropy',metrics=['accuracy'])

##### Prepare data for training

In [ ]:
from sklearn.model_selection import train_test_split, KFold
from tensorflow.keras.utils import to_categorical

num_classes = 23  # Updated number of classes to 23
labels = to_categorical(labels, num_classes)

# Train the model with K-Fold Cross-Validation
kf = KFold(n_splits=3)
for train_index, test_index in kf.split(data):
    x_train, x_test = data[train_index], data[test_index]
    y_train, y_test = labels[train_index], labels[test_index]
    print(x_train.shape)

In [ ]:
# Train the model
history = model.fit(x_train, y_train, epochs=25)
    
    # Evaluate the model
model.evaluate(x_test, y_test)

    # Save the model
model.save('23class.h5')

In [ ]:
labels.shape

##### Evaluate and plot the results

In [ ]:
y_pred = model.predict(x_test)
y_pred_classes = np.argmax(y_pred, axis=1)
y_true_classes = np.argmax(y_test, axis=1)

confusion_matrix_result = confusion_matrix(y_true_classes, y_pred_classes)

train_accuracy = history.history['accuracy']
train_loss = history.history['loss']
val_accuracy = history.history['val_accuracy']
val_loss = history.history['val_loss']

epochs = range(len(train_accuracy))
plt.figure(figsize=(12, 4))

#### Plotting the accuracy and loss

In [ ]:
plt.subplot(1, 2, 1)
plt.plot(epochs, train_accuracy, 'b', label='Training accuracy')
plt.plot(epochs, val_accuracy, 'r', label='Validation accuracy')
plt.title('Accuracy')
plt.xlabel('Epoch')
plt.ylabel('Accuracy')
plt.legend(['Train', 'Validation'], loc='lower right')

# Plotting the loss
plt.subplot(1, 2, 2)
plt.plot(epochs, train_loss, 'b', label='Training loss')
plt.plot(epochs, val_loss, 'r', label='Validation loss')
plt.title('Loss')
plt.xlabel('Epoch')
plt.ylabel('Loss')
plt.legend(['Train', 'Validation'], loc='upper right')

plt.show()

In [ ]:

# for i in range(3):
#     x_train,x_test, y_train, y_test=train_test_split(data, label, test_size=0.2,random_state = np.random.randint(1,1000, 1)[0])
#     print(x_train.shape)
#     # let's make all layers non-trainable
#     for layer in vgg_model.layers :
#         layer.trainable = False
#     features_train=vgg_model.predict(x_train)
#     features_test=vgg_model.predict(x_test)
#     print(features_train.shape)
#     num_train=x_train.shape[0]
#     num_test=x_test.shape[0]
#     print(num_train)
#     print(num_test)
#     x_test=features_test.reshape(num_test,-1)
#     x_train=features_train.reshape(num_train,-1)
#     print(x_train.shape)
#     print(x_train.shape)
#     #x_train,x_valid,y_train,y_valid= train_test_split(x_train, y_train, test_size=0.1,random_state = np.random.randint(1,1000, 1)[0])
# #     history=model.fit(x_train,y_train,epochs=15,batch_size=32,verbose=1)
# #     model.evaluate(x_test,y_test)

In [ ]:
history = model.fit(x_train, y_train, epochs=25)


In [ ]:
model.save('6claass.h5')

In [ ]:
from sklearn.metrics import classification_report, confusion_matrix, roc_curve, auc
from mlxtend.plotting import plot_confusion_matrix

In [ ]:
y_pred=model.predict(x_test)

In [ ]:
y_pred2=np.argmax(y_pred, axis=1)
y_pred2

In [ ]:
y_test=np.argmax(y_test, axis=1)

In [ ]:
y_test

In [ ]:
confusion_matrix_result=confusion_matrix(y_test,y_pred2)

In [ ]:
import seaborn as sns
import matplotlib.pyplot as plt
import pylab as pl
plt.title("skin detection  using VGG19 ")

ax= plt.subplot()
sns.heatmap(confusion_matrix_result, annot=True, fmt='g', ax=ax);
pl.show()

In [ ]:
train_accuracy = history.history['accuracy']
#val_accuracy = history.history['val_accuracy']
train_loss = history.history['loss']
#val_loss = history.history['val_loss']

epochs = range(len(train_accuracy))
plt.figure(figsize=(12,4))
# Plotting the accuracy
plt.subplot(1,2,1)
plt.plot(epochs, train_accuracy, 'b', label='Training accuracy')

plt.title('accuracy')
plt.xlabel('Epoch')
plt.ylabel('Accuracy')
plt.legend(['train', 'val'], loc='lower right')

# Plotting the loss
plt.subplot(1,2,2)
plt.plot(epochs, train_loss, 'b', label='Training loss')

plt.title('Loss ')
plt.xlabel('Epoch')
plt.ylabel('Loss')
plt.legend(['train', 'val'], loc='upper right')

In [ ]:
import os
import matplotlib.pyplot as plt
import cv2
from tensorflow.keras.models import Model, Sequential
from tensorflow.keras.layers import Input, Convolution2D, ZeroPadding2D,MaxPooling2D, Flatten, Dense, Dropout, Activation
from PIL import Image
import numpy as np
from tensorflow.keras.preprocessing.image import load_img, save_img, img_to_array
from tensorflow.keras.applications.imagenet_utils import preprocess_input
from tensorflow.keras.preprocessing import image
import pandas as pd
import tensorflow as tf
import keras
import pickle

In [ ]:
confusion_matrix=classification_report(y_test,y_pred2)

In [ ]:
print(confusion_matrix)

In [ ]:
import tensorflow as tf
import numpy as np
import cv2

import tensorflow as tf
import numpy as np
import cv2

def predict_skin_disease(image_path):
    # Load saved model
    model = tf.keras.models.load_model('6claass.h5')

    # Load and preprocess image
    img = cv2.imread(image_path)
    img = cv2.resize(img, (180, 180))
    img = np.array(img) / 255.0
    img = np.expand_dims(img, axis=0)
    img=vgg_model.predict(img)
    img=img.reshape(1,-1)

    # Make prediction on preprocessed image
    pred = model.predict(img)[0]
    predicted_class = np.argmax(pred)

    return predicted_class


print(predict_skin_disease("/kaggle/input/skindatasets/skin/test/Normal/0_0_aidai_0029.jpg"))

In [ ]:
print(y_train)

In [ ]:
import tensorflow as tf
import numpy as np
import cv2

def predict_skin_disease(image_path):
    # Define list of class names
    class_names = ["Acne","Eczema","Atopic","Psoriasis","Tinea","vitiligo"]

    # Load saved model
    model = tf.keras.models.load_model('6claass.h5')

    # Load and preprocess image
    img = cv2.imread(image_path)
    img = cv2.resize(img, (180, 180))
    img = np.array(img) / 255.0
    img = np.expand_dims(img, axis=0)
    img = vgg_model.predict(img)
    img = img.reshape(1, -1)

    # Make prediction on preprocessed image
    pred = model.predict(img)[0]
    predicted_class_index = np.argmax(pred)
    predicted_class_name = class_names[predicted_class_index]

    return predicted_class_name

print(predict_skin_disease("/kaggle/input/dermnet/test/Atopic Dermatitis Photos/03ichthyosis050127.jpg"))
